In [1]:
#Set working directory
import os
os.chdir('/scratch/sjw6257/KG2_vs_DrugMechDB') 

# Install required packages
import pandas as pd
import matplotlib.pyplot as plt
import yaml
import sys 
import csv
import json

from graph_tool.all import *

In [2]:
# Optional
#pip install tqdm

from tqdm.notebook import tqdm
import itertools
from itertools import product

import math
from collections import defaultdict

In [3]:
# Load edge list
import dask.dataframe as dd

file_path = 'KG2.9.0c/combined_edge.csv'

columns_to_read = ['subject', 'object']
df_graph = dd.read_csv(file_path, sep=',', usecols=columns_to_read)


## 1. Create Vertices Combination

In [4]:
# Load Entity Aligned nodes
import ast
import itertools

# Load Entity Aligned nodes (Input file)
df_vert = dd.read_csv('Entity_analysis/KG2.9.0c/sorted_graph_DrugMechDB.csv', sep=",")

# Compute the DataFrame 
v_df = df_vert[['graph_id', 'c_ids']].compute()

# Convert the string representation of lists into actual lists
v_df['c_ids'] = v_df['c_ids'].apply(ast.literal_eval)

# Create a dictionary with graph_id as keys and c_ids as values
v_dict = v_df.set_index('graph_id')['c_ids'].to_dict()

In [5]:
# For each graph, generate vertecies pair combinations
pair_vert = {}
for key, c_ids_list in v_dict.items():
    # Generate all possible pairs from the list of c_ids
    pairs = list(itertools.combinations(c_ids_list, 2))
    pair_vert[key] = pairs

In [6]:
# Optional: Confirm all graphs are loaded
print("Number of graphs: ", len(pair_vert))

Number of graphs:  691


## 2. Load KG2

In [7]:
%time g = load_graph("KG2.9.0c/KG2.9.0c.gt")

print(g) # To check the graph is loaded properly

CPU times: user 13.9 s, sys: 7.7 s, total: 21.6 s
Wall time: 21.5 s
<Graph object, undirected, with 22538515 vertices and 46651431 edges, 1 internal vertex property, at 0x7f825c0f79b0>


In [8]:
## Vertex property map
print("Available vertex property maps:")
for prop_name in g.vp.keys():
    print(prop_name)

Available vertex property maps:
label


## 3. 2-hop Neighborhood  Assessment

In [9]:
# Use 'label' as the node ID property map
node_id_prop = g.vp['label']

# Create a mapping from node IDs to vertex objects
node_id_to_vertex = {}
for v in g.vertices():
    node_id = node_id_prop[v]
    node_id_to_vertex[node_id] = v

In [10]:
## Initialize a dictionary to store the paths, node pairs, and relative information
paths_dict = {}
two_hop = defaultdict(list)
no_path = defaultdict(list)
missing_nodes = []

# Function to check if a value is NaN
def is_nan(value):
    if value is None:
        return True
    try:
        # Check for float NaN
        return math.isnan(float(value))
    except:
        # Check for string NaN
        return str(value).strip().lower() == 'nan'

In [11]:
### Two hop code ###
for key in tqdm(pair_vert.keys(), desc='Processing keys'):
    pairs_list = pair_vert[key]
    paths_dict[key] = {}
    # Wrap the inner loop with tqdm to track progress over pairs
    for source_id, target_id in tqdm(pairs_list, desc=f'Processing pairs for key {key}', leave=False):
        # Ensure node IDs are strings if they are stored as strings in the property map
        source_id_str = str(source_id)
        target_id_str = str(target_id)
        source = node_id_to_vertex.get(source_id_str)
        target = node_id_to_vertex.get(target_id_str)
        if source is None or target is None:
            # Source or target not in graph
            paths_dict[key][(source_id, target_id)] = None
            # Record the missing node(s)
            missing_node_info = {
                'key': key,
                'source_id': source_id,
                'target_id': target_id,
                'missing_node': 'source' if source is None and target is not None else
                                 'target' if target is None and source is not None else
                                 'both'
            }
            missing_nodes.append(missing_node_info)
            print(f"Source or target not in graph for key '{key}': source_id={source_id}, target_id={target_id}")
            # Add the pair to pairs_no_valid_path
            no_path[key].append((source_id, target_id))
            continue
            
        # Set the cutoff to 2
        cutoff = 2
        unique_paths = set()
        paths = []
        
        # Use Graph-tool's all_paths function with cutoff=2
        for p in all_paths(g, source, target, cutoff=cutoff):
            # Convert vertices back to node IDs
            path_node_ids = [node_id_prop[v] for v in p]
            # Skip paths that contain NaN
            if any(is_nan(node_id) for node_id in path_node_ids):
                continue
            # Add the path if it's not a duplicate
            path_tuple = tuple(path_node_ids)
            if path_tuple not in unique_paths:
                unique_paths.add(path_tuple)
                paths.append(path_node_ids)
                found_any_path = True
        if paths:
            # Store the paths in paths_dict
            paths_dict[key][(source_id, target_id)] = paths
            # Add the pair to the list for each graph
            two_hop[key].append((source_id, target_id))
            print(f"Paths found between {source_id} and {target_id}: {len(paths)} paths")
        else:
            # No valid path found with cutoff=2
            paths_dict[key][(source_id, target_id)] = None
            no_path[key].append((source_id, target_id))
            print(f"No valid paths found between {source_id} and {target_id}")

Processing keys:   0%|          | 0/691 [00:00<?, ?it/s]

Processing pairs for key DB08842_MESH_D000544_1:   0%|          | 0/210 [00:00<?, ?it/s]

No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0007271
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0035249
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0005947
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0004129
Paths found between PUBCHEM.COMPOUND:7045767 and CHEBI:26519: 12 paths
Paths found between PUBCHEM.COMPOUND:7045767 and UMLS:C0132173: 7 paths
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0018393
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0006979
Paths found between PUBCHEM.COMPOUND:7045767 and HP:0025464: 8 paths
No valid paths found between PUBCHEM.COMPOUND:7045767 and GO:0007613
No valid paths found between PUBCHEM.COMPOUND:7045767 and CHEBI:64645
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=PUBCHEM.COMPOUND:7045767, target_id=EFO:0005816
No valid paths found between PUBCHEM.COMPOUND:7045767 and PR:000010173
No valid paths found between PUBCHEM.COMPO

Processing pairs for key DB00193_MESH_D010003_1:   0%|          | 0/190 [00:00<?, ?it/s]

Paths found between PUBCHEM.COMPOUND:33741 and NCBIGene:4988: 19 paths
Paths found between PUBCHEM.COMPOUND:33741 and NCBIGene:111: 6 paths
Paths found between PUBCHEM.COMPOUND:33741 and NCBIGene:3767: 5 paths
No valid paths found between PUBCHEM.COMPOUND:33741 and GO:0070509
No valid paths found between PUBCHEM.COMPOUND:33741 and GO:1990793
No valid paths found between PUBCHEM.COMPOUND:33741 and GO:0061535
No valid paths found between PUBCHEM.COMPOUND:33741 and GO:0099610
No valid paths found between PUBCHEM.COMPOUND:33741 and CL:0000198
Paths found between PUBCHEM.COMPOUND:33741 and NCBIGene:6530: 11 paths
Paths found between PUBCHEM.COMPOUND:33741 and GO:0051620: 1 paths
Paths found between PUBCHEM.COMPOUND:33741 and PUBCHEM.COMPOUND:439260: 9 paths
No valid paths found between PUBCHEM.COMPOUND:33741 and GO:0061533
Paths found between PUBCHEM.COMPOUND:33741 and NCBIGene:6532: 14 paths
Paths found between PUBCHEM.COMPOUND:33741 and GO:0051610: 1 paths
Paths found between PUBCHEM.COMP

...

Paths found between PUBCHEM.COMPOUND:21867154 and NCBIGene:1128: 104 paths
Paths found between PUBCHEM.COMPOUND:21867154 and NCBIGene:1129: 96 paths
Paths found between PUBCHEM.COMPOUND:21867154 and NCBIGene:1131: 93 paths
Paths found between PUBCHEM.COMPOUND:21867154 and GO:0095500: 3 paths
Paths found between PUBCHEM.COMPOUND:21867154 and PUBCHEM.COMPOUND:187: 105 paths
Paths found between PUBCHEM.COMPOUND:21867154 and GO:0001696: 19 paths
Paths found between PUBCHEM.COMPOUND:21867154 and MONDO:0004247: 84 paths
Paths found between PUBCHEM.COMPOUND:21867154 and UBERON:0000945: 8 paths
Paths found between PUBCHEM.COMPOUND:21867154 and MONDO:0001126: 46 paths
Paths found between NCBIGene:1128 and NCBIGene:1129: 212 paths
Paths found between NCBIGene:1128 and NCBIGene:1131: 239 paths
Paths found between NCBIGene:1128 and GO:0095500: 2 paths
Paths found between NCBIGene:1128 and PUBCHEM.COMPOUND:187: 33 paths
Paths found between NCBIGene:1128 and GO:0001696: 19 paths
Paths found between 

Processing pairs for key DB00937_MESH_D009765_1:   0%|          | 0/45 [00:00<?, ?it/s]

Paths found between PUBCHEM.COMPOUND:7029 and NCBIGene:6530: 91 paths
Paths found between PUBCHEM.COMPOUND:7029 and NCBIGene:6531: 70 paths
Paths found between PUBCHEM.COMPOUND:7029 and GO:0051620: 2 paths
Paths found between PUBCHEM.COMPOUND:7029 and GO:0090494: 1 paths
Paths found between PUBCHEM.COMPOUND:7029 and PUBCHEM.COMPOUND:439260: 827 paths
Paths found between PUBCHEM.COMPOUND:7029 and PUBCHEM.COMPOUND:681: 835 paths
No valid paths found between PUBCHEM.COMPOUND:7029 and PUBCHEM.COMPOUND:16132350
Paths found between PUBCHEM.COMPOUND:7029 and HP:0002591: 7 paths
Paths found between PUBCHEM.COMPOUND:7029 and MONDO:0011122: 128 paths
Paths found between NCBIGene:6530 and NCBIGene:6531: 281 paths
Paths found between NCBIGene:6530 and GO:0051620: 3 paths
Paths found between NCBIGene:6530 and GO:0090494: 2 paths
Paths found between NCBIGene:6530 and PUBCHEM.COMPOUND:439260: 143 paths
Paths found between NCBIGene:6530 and PUBCHEM.COMPOUND:681: 147 paths
No valid paths found between 

Processing pairs for key DB00620_MESH_D004892_1:   0%|          | 0/45 [00:00<?, ?it/s]

Paths found between PUBCHEM.COMPOUND:6216 and NCBIGene:2908: 52 paths
Paths found between PUBCHEM.COMPOUND:6216 and NCBIGene:301: 31 paths
Paths found between PUBCHEM.COMPOUND:6216 and NCBIGene:5321: 19 paths
Paths found between PUBCHEM.COMPOUND:6216 and NCBIGene:5742: 35 paths
Paths found between PUBCHEM.COMPOUND:6216 and NCBIGene:5743: 65 paths
No valid paths found between PUBCHEM.COMPOUND:6216 and GO:0019370
No valid paths found between PUBCHEM.COMPOUND:6216 and GO:0001516
Paths found between PUBCHEM.COMPOUND:6216 and GO:0006954: 2 paths
Paths found between PUBCHEM.COMPOUND:6216 and MONDO:0006545: 3 paths
Paths found between NCBIGene:2908 and NCBIGene:301: 272 paths
Paths found between NCBIGene:2908 and NCBIGene:5321: 184 paths
Paths found between NCBIGene:2908 and NCBIGene:5742: 227 paths
Paths found between NCBIGene:2908 and NCBIGene:5743: 388 paths
No valid paths found between NCBIGene:2908 and GO:0019370
Paths found between NCBIGene:2908 and GO:0001516: 1 paths
Paths found betwe

#### Optional 1: Print the compiled pairs that have paths with 2-hop
for key, pairs in two_hop.items():
    print(f"{key} with 2-hop paths: {pairs} \nThere are ", len(pairs),"pairs.")
    print()

#### Optional 2: Print the intermediary path for each node pair
for key, pairs in paths_dict.items():
    print(f"{key}")
    for pair, paths in pairs.items():
        print(f"  Pair: {pair}")
        if paths is not None:
            print(f"    Paths (cutoff = 2): {paths}")
            print()
        else:
            print("    No path found with 2-hop or nodes missing.")
            print()

In [12]:
# Save 2-hop path edge-list to JSON file
save_dir = 'network_analysis/k_hop_graph'
file_path = os.path.join(save_dir, 'KG2.9.0_two-hop.json') # define file path

### Note: The file contains both well-connected and disconnected graphs
with open(file_path, 'w', encoding='utf-8') as json_file:
    json.dump(two_hop, json_file, indent=2)

print("\nPairs with 2-hop paths have been saved to 'KG2.9.0_two-hop.json'.")


Pairs with 2-hop paths have been saved to 'KG2.9.0_two-hop.json'.


### Find disconnected graph(s) and their components

In [13]:
import networkx as nx

def load_data(two_hop_file):
    with open(two_hop_file, 'r') as f:
        data = json.load(f)
    return data

def build_graph(edges):
    graph = nx.Graph()
    graph.add_edges_from(edges)
    return graph

def find_disconnected_keys(data):
    disconnected_keys = {}

    for key, edges in data.items():
        graph = build_graph(edges)
        components = [list(component) for component in nx.connected_components(graph) if len(component) > 1]
        if len(components) > 1:
            disconnected_keys[key] = components

    return disconnected_keys

two_hop_file = os.path.join(save_dir, 'KG2.9.0_two-hop.json')  # Update with the correct path
data = load_data(two_hop_file)
disconnected_keys = find_disconnected_keys(data)

In [14]:
## Optional if you want to see which graph(s) is/are disconnected
#disconnected_keys

## 4. Generate pair combination not captured by 2-hop

In [15]:
# Generate pair combination from disconnected graph
def generate_pairs(disconnected_keys):
    output_dict = {}
    for key, lists in disconnected_keys.items():
        output_dict[key] = list(product(*lists))
    return output_dict
component_pairs = generate_pairs(disconnected_keys)

In [16]:
# Extract nodes that are not captured by 2-hop
non_two_hop_nodes = {}

# Iterate over each key in two_hop
for key in two_hop:
    # Check if the key exists in v_dict
    if key in v_dict:
        v_nodes = set(v_dict[key])  # Nodes from v_dict for this key
    else:
        # If the key is not in v_dict, skip it or handle as needed
        print(f"Key {key} is in two_hop but not in v_dict")
        continue
    
    two_hop_pairs = two_hop[key]  # Get two-hop pairs for the key
    
    # Collect all nodes involved in the two-hop pairs
    two_hop_nodes = set()
    for pair in two_hop_pairs:
        two_hop_nodes.update(pair)
    
    # Find nodes that are in v_nodes but not in two_hop_nodes
    missing_nodes = v_nodes - two_hop_nodes
    if missing_nodes:
        non_two_hop_nodes[key] = list(missing_nodes)

In [17]:
## Create the node pair combinations that were not captured in 2-hop process (non_two_hop_nodes)
node_pairs = {}
for key in non_two_hop_nodes:
    node_pairs[key] = []
    for v_node in v_dict[key]:
        for non_two_hop_node in non_two_hop_nodes[key]:
            if v_node != non_two_hop_node:  # Exclude pairs with identical elements
                node_pairs[key].append((v_node, non_two_hop_node))

In [18]:
### Create node combination for 3-hop analysis
# Combine node_pairs and component_pairs. If the keys match combine the list, make sure no tuples are duplicated/same.
combined_pairs = {}

# Combine node_pairs into combined_pairs
for key, value in node_pairs.items():
    if key not in combined_pairs:
        combined_pairs[key] = set(value)  # Use a set to avoid duplicates
    else:
        combined_pairs[key].update(value)

# Combine component_pairs into combined_pairs
for key, value in component_pairs.items():
    if key not in combined_pairs:
        combined_pairs[key] = set(value)  # Use a set to avoid duplicates
    else:
        combined_pairs[key].update(value)

for key in combined_pairs:
    combined_pairs[key] = list(combined_pairs[key])

Note: `combined_pairs` should contain the merged data without duplicated tuples.

## 5. Three-hop Neighborhood Assessment
Using the node pair combination from above step, assess if there are path within 3-hop.

#### Note: 
This code will not generate intermediary node and path due to memory and time efficiency purpose. It will return tuples if 3-hop path exist in the vertex pair. 

In [19]:
paths_dict_3 = {}
three_hop = {}
no_path_3 = {}
missing_nodes_3 = []

# Set the maximum number of paths per node pair
max_paths_per_pair = 2

# Wrap the outer loop with tqdm to track progress 
for key in tqdm(combined_pairs.keys(), desc='Processing keys'):
    pairs_list = combined_pairs[key]
    paths_dict_3[key] = {}
    three_hop[key] = []  
    no_path_3[key] = []   # Initialize an empty list for each key
    
    for source_id, target_id in tqdm(pairs_list, desc=f'Processing pairs for key {key}', leave=False):
        # Ensure node IDs are strings if they are stored as strings in the property map
        source_id_str = str(source_id)
        target_id_str = str(target_id)
        source = node_id_to_vertex.get(source_id_str)
        target = node_id_to_vertex.get(target_id_str)
        
        if source is None or target is None:
            # Source or target not in graph
            paths_dict_3[key][(source_id, target_id)] = None
            # Record the missing node(s)
            missing_node_info = {
                'key': key,
                'source_id': source_id,
                'target_id': target_id,
                'missing_node': 'source' if source is None and target is not None else
                                 'target' if target is None and source is not None else
                                 'both'
            }
            missing_nodes_3.append(missing_node_info)
            print(f"Source or target not in graph for key '{key}': source_id={source_id}, target_id={target_id}")
            # Add the pair to pairs_no_valid_path
            no_path_3[key].append((source_id, target_id))
            continue
            
        # Check if a path exists within 3 hops
        distance = shortest_distance(g, source=source, target=target, directed=False)
        if distance <= 3:
            paths_dict_3[key][(source_id, target_id)] = distance
            three_hop[key].append((source_id, target_id))
            print(f"Path found between {source_id} and {target_id} with length {distance}")
        else:
            paths_dict_3[key][(source_id, target_id)] = None
            no_path_3[key].append((source_id, target_id))
            print(f"No path found between {source_id} and {target_id} within 3 hops")

Processing keys:   0%|          | 0/86 [00:00<?, ?it/s]

Processing pairs for key DB08842_MESH_D000544_1:   0%|          | 0/40 [00:00<?, ?it/s]

Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=GO:0006979, target_id=CHEBI:60425
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=MONDO:0004975, target_id=EFO:0005816
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=GO:0007271, target_id=CHEBI:60425
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=GO:0035249, target_id=CHEBI:60425
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=PR:000010173, target_id=EFO:0005816
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=HP:0002185, target_id=EFO:0005816
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=EFO:0005816, target_id=CHEBI:60425
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=PUBCHEM.COMPOUND:7045767, target_id=CHEBI:60425
Source or target not in graph for key 'DB08842_MESH_D000544_1': source_id=GO:0018393, target_id=EFO:0005816
Source o

Processing pairs for key DB00193_MESH_D010003_1:   0%|          | 0/19 [00:00<?, ?it/s]

Path found between PUBCHEM.COMPOUND:5202 and CL:0000198 with length 3
Path found between NCBIGene:6532 and CL:0000198 with length 3
No path found between PUBCHEM.COMPOUND:33741 and CL:0000198 within 3 hops
No path found between GO:1990793 and CL:0000198 within 3 hops
Path found between NCBIGene:6530 and CL:0000198 with length 3
Path found between PUBCHEM.COMPOUND:439260 and CL:0000198 with length 3
No path found between NCBIGene:3767 and CL:0000198 within 3 hops
No path found between GO:0061535 and CL:0000198 within 3 hops
No path found between GO:0051610 and CL:0000198 within 3 hops
Path found between HP:0012531 and CL:0000198 with length 3
Path found between NCBIGene:111 and CL:0000198 with length 3
No path found between GO:0060096 and CL:0000198 within 3 hops
Path found between MONDO:0005178 and CL:0000198 with length 3
No path found between GO:0061533 and CL:0000198 within 3 hops
No path found between GO:0070509 and CL:0000198 within 3 hops
No path found between GO:0051620 and CL:0

...

Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=GO:0070509, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=NCBIGene:7421, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=CL:0000092, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=GO:0045453, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=HP:0002901, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=PUBCHEM.COMPOUND:5280793, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=MONDO:0005298, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D010024_1': source_id=PUBCHEM.COMPOUND:9547243

Processing pairs for key DB00153_MESH_D015663_1:   0%|          | 0/20 [00:00<?, ?it/s]

Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=GO:0070509, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Path found between PUBCHEM.COMPOUND:9547243 and GO:0035898 with length 3
Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=CHEMBL.COMPOUND:CHEMBL4850142, target_id=GO:0035898
No path found between CL:0000092 and GO:0035898 within 3 hops
Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=GO:0070561, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=GO:0045453, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Path found between NCBIGene:7421 and GO:0035898 with length 3
Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=HP:0002901, target_id=CHEMBL.COMPOUND:CHEMBL4850142
Path found between MONDO:0008159 and GO:0035898 with length 3
Source or target not in graph for key 'DB00153_MESH_D015663_1': source_id=PUBCHEM.COMPOUND:5280793, target_id=C

Processing pairs for key DB05676_MESH_D015535_1:   0%|          | 0/22 [00:00<?, ?it/s]

No path found between NCBIGene:5143 and GO:0032627 within 3 hops
No path found between NCBIGene:5144 and GO:0032627 within 3 hops
No path found between NCBIGene:5141 and GO:0032627 within 3 hops
No path found between NCBIGene:5142 and GO:0032627 within 3 hops
No path found between GO:0006198 and GO:0032613 within 3 hops
Path found between PUBCHEM.COMPOUND:6076 and GO:0032613 with length 3
Path found between MONDO:0011849 and GO:0032613 with length 3
No path found between NCBIGene:4843 and GO:0032627 within 3 hops
Path found between NCBIGene:5144 and GO:0032613 with length 3
Path found between NCBIGene:5141 and GO:0032613 with length 3
No path found between NCBIGene:5143 and GO:0032613 within 3 hops
No path found between PUBCHEM.COMPOUND:11561674 and GO:0032627 within 3 hops
Path found between NCBIGene:5142 and GO:0032613 with length 3
Path found between NCBIGene:4843 and GO:0032613 with length 3
Path found between PUBCHEM.COMPOUND:11561674 and GO:0032613 with length 3
Path found betwee

In [22]:
output_path = os.path.join(save_dir, 'KG2.9.0_three-hop.json') # define file path

with open(output_path, 'w', encoding='utf-8') as json_file:
    json.dump(three_hop, json_file, indent=4)

print(f"The three_hop data has been saved in {output_path}")

The three_hop data has been saved in network_analysis/k_hop_graph/KG2.9.0_three-hop.json


### Combine 2 and 3 hops node pairs (k-hop)

In [23]:
# Combine 2 and 3 hops node pairs (k-hop)
k_hop = defaultdict(list)

# Add two_hop entries to k_hop
for key, value_list in two_hop.items():
    k_hop[key].extend(value for value in value_list if value not in k_hop[key])

# Add three_hop entries and combine
for key, value_list in three_hop.items():
    k_hop[key].extend(value for value in value_list if value not in k_hop[key])

# Print the combined dictionary
for key, value in k_hop.items():
    print(f"{key}: {value} \nThere are ", len(value),"pairs.")
    print()

DB08842_MESH_D000544_1: [('PUBCHEM.COMPOUND:7045767', 'CHEBI:26519'), ('PUBCHEM.COMPOUND:7045767', 'UMLS:C0132173'), ('PUBCHEM.COMPOUND:7045767', 'HP:0025464'), ('PUBCHEM.COMPOUND:7045767', 'MONDO:0001152'), ('PUBCHEM.COMPOUND:7045767', 'HP:0002185'), ('PUBCHEM.COMPOUND:7045767', 'MONDO:0004975'), ('GO:0007271', 'GO:0035249'), ('GO:0007271', 'GO:0006979'), ('GO:0007271', 'GO:0007613'), ('GO:0007271', 'GO:0014055'), ('GO:0007271', 'MONDO:0001152'), ('GO:0007271', 'HP:0002185'), ('GO:0007271', 'MONDO:0004975'), ('GO:0035249', 'GO:0006979'), ('GO:0035249', 'GO:0007613'), ('GO:0035249', 'GO:0061535'), ('GO:0035249', 'GO:0150076'), ('GO:0035249', 'MONDO:0001152'), ('GO:0035249', 'MONDO:0004975'), ('GO:0005947', 'MONDO:0004975'), ('GO:0004129', 'GO:0006979'), ('GO:0004129', 'MONDO:0001152'), ('GO:0004129', 'MONDO:0004975'), ('CHEBI:26519', 'UMLS:C0132173'), ('CHEBI:26519', 'GO:0006979'), ('CHEBI:26519', 'HP:0025464'), ('CHEBI:26519', 'PR:000010173'), ('CHEBI:26519', 'MONDO:0001152'), ('CHEBI

In [24]:
f_path = os.path.join(save_dir, 'KG2.9.0_k-hop.json') # define file path

with open(f_path, 'w', encoding='utf-8') as json_file:
    json.dump(k_hop, json_file, indent=2)

print(f"Pairs with 2 and 3-hop paths have been saved to {f_path}")

Pairs with 2 and 3-hop paths have been saved to network_analysis/k_hop_graph/KG2.9.0_k-hop.json


In [25]:
# Nodes NOT captured in both two-hop and three-hop paths
non_k_hop_nodes = {}

# Iterate over each key in v_dict
for key in v_dict:
    v_nodes = set(v_dict[key])  # Nodes from v_dict for this key
    
    # Get two-hop and three-hop pairs for the key, or empty list if the key is not present
    two_hop_pairs = two_hop.get(key, [])
    three_hop_pairs = three_hop.get(key, [])
    
    # Collect all nodes involved in the two-hop pairs
    two_hop_nodes = set()
    for pair in two_hop_pairs:
        two_hop_nodes.update(pair)
    
    # Collect all nodes involved in the three-hop pairs
    three_hop_nodes = set()
    for pair in three_hop_pairs:
        three_hop_nodes.update(pair)
    
    # Union of nodes involved in two-hop and three-hop pairs
    hop_nodes = two_hop_nodes.union(three_hop_nodes)
    
    # Find nodes that are in v_nodes but not in hop_nodes
    missing = v_nodes - hop_nodes
    if missing:
        non_k_hop_nodes[key] = list(missing)


In [26]:
f_path_2 = os.path.join(save_dir, 'KG2.9.0_non_k_hop_nodes.json') # define file path

with open(f_path_2, 'w', encoding='utf-8') as json_file:
    json.dump(non_k_hop_nodes, json_file, indent=2)

print(f"Pairs with no 2 and 3-hop paths have been saved to {f_path_2}.")
print("There are ",len(non_k_hop_nodes),"graphs.")

Pairs with 2 and 3-hop paths have been saved to network_analysis/k_hop_graph/KG2.9.0_non_k_hop_nodes.json.
There are  26 graphs.


## Spanning tree

In [27]:
k_hop_file = os.path.join(save_dir, 'KG2.9.0_k-hop.json')

# Load the JSON data
with open(k_hop_file, 'r', encoding='utf-8') as f:
    data = json.load(f)

# Initialize collections for connected and disconnected graphs
connected_graphs_data = []
disconnected_graphs = {}

# Loop over each key in the data
for key, node_pairs in data.items():
    # Create an undirected graph
    G = nx.Graph()

    # Add edges to the graph
    G.add_edges_from([tuple(pair) for pair in node_pairs])

    # Skip if there are no node pairs
    if not node_pairs:
        print(f"No node pairs found for key '{key}'. Skipping.")
        continue

    # The starting node is the first node of the first tuple
    start_node = node_pairs[0][0]

    # Skip if the starting node is not in the graph
    if start_node not in G:
        print(f"Starting node '{start_node}' not found in the graph for key '{key}'. Skipping.")
        continue

    # Check if the graph is connected
    if nx.is_connected(G):
        # Process connected graph
        output_data = {
            'graph_id': key,
            'links': [],
            'nodes': [],
            'Tree Count Profile': {}
        }

        # Compute a DFS tree of the graph
        dfs_tree = nx.dfs_tree(G, source=start_node).to_undirected()

        # Get the number of nodes and edges in the DFS tree
        node_count = dfs_tree.number_of_nodes()
        edge_count = dfs_tree.number_of_edges()

        # Populate the 'links' section
        output_data['links'] = [
            {'source': u, 'target': v} for u, v in dfs_tree.edges()
        ]

        # Populate the 'nodes' section
        output_data['nodes'] = list(dfs_tree.nodes())

        # Populate the 'Tree Count Profile'
        output_data['Tree Count Profile'] = {
            'Node': node_count,
            'Edge': edge_count
        }

        # Add the graph data to the connected graphs list
        connected_graphs_data.append(output_data)
    else:
        print(f"Graph '{key}' is disconnected.")
        # Process disconnected graph
        # Get connected components and convert each to a list of nodes
        components = [list(component) for component in nx.connected_components(G)]
        # Store the components in the dictionary with the graph ID as the key
        disconnected_graphs[key] = components

print("\nDisconnected Graphs Components:")
if disconnected_graphs:
    for graph_id, components in disconnected_graphs.items():
        print(f"Graph ID: {graph_id}")
        for i, component in enumerate(components, start=1):
            print(f"  Component {i}: {component}")
else:
    print("No disconnected graphs found.")


Disconnected Graphs Components:
No disconnected graphs found.


In [28]:
connected_f_path = os.path.join(save_dir, 'KG2.9.0_connected_tree.yaml')

# Save connected graphs data to a YAML file (final output file)
with open(connected_f_path, 'w') as f:
    yaml.dump(connected_graphs_data, f, sort_keys=False)
print(f"Connected graphs data saved to '{connected_f_path}'.")

Connected graphs data saved to 'network_analysis/k_hop_graph/KG2.9.0_connected_tree.yaml'.


In [ ]:
# Save disconnected graphs components to a JSON file
disconnected_f_path = os.path.join(save_dir, 'KG2.9.0_disconnect.json')
with open(disconnected_f_path, 'w') as f:
    json.dump(disconnected_graphs, f, indent=3)

print(f"Disconnected graphs data saved to '{disconnected_f_path}'.")